In [38]:
from pathlib import Path

from ax.utils.notebook.plotting import render, init_notebook_plotting
from ax.plot.contour import interact_contour
from ax.plot.trace import optimization_trace_single_method
from ax.plot.slice import plot_slice
import numpy as np
from optiwrap import load_experiment_config, scheduler_from_json_file
import plotly.graph_objects as go
import yaml

from fetch3.optimize.fetch_wrapper import get_model_obs

init_notebook_plotting()

[INFO 05-12 15:33:38] ax.utils.notebook.plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


In [40]:
config_path = Path().resolve() / "config_files/opt_umbs_M8.yml"

In [41]:
scheduler_fp = Path("/Users/jmissik/Desktop/repos/fetch3_nhl/output/UMBS_test_Ameriflux_M8_20220512T144509/scheduler.json")
experiment_dir = scheduler_fp.parent

In [42]:
scheduler = scheduler_from_json_file(scheduler_fp)
experiment = scheduler.experiment

In [43]:
best_trial, best_params, obj = scheduler.get_best_trial()
best_trial

0

In [44]:
experiment.fetch_data().df

arm_name         metric_name           mean  sem  trial_index
0      0_0  mean_squared_error  109322.432699  0.0            0

In [27]:
metric_name = "mean_squared_error"
model = scheduler.generation_strategy.model
render(interact_contour(model=model, metric_name=metric_name), True)

In [28]:
render(plot_slice(model, model.parameters[0], metric_name))

In [45]:

best_objectives = np.array([[trial.objective_mean for trial in experiment.trials.values()]])
best_objective_plot = optimization_trace_single_method(
    y=np.minimum.accumulate(best_objectives, axis=1),
    title="Model performance vs. # of iterations",
    ylabel="Output",
)
render(best_objective_plot)

In [47]:
ex_config_file = "opt_umbs_M8.yml"
best_trial, best_params, obj = scheduler.get_best_trial()
dir_best_trial = (experiment_dir / str(best_trial).zfill(6))

model_file = dir_best_trial / "sapflux.nc"

config_file = dir_best_trial / "config.yml"
with open(config_file, "r") as yml_config:
    model_cfg = yaml.safe_load(yml_config)

config = load_experiment_config(experiment_dir / ex_config_file)

In [48]:
ex_settings = config["optimization_options"]
obs_file = ex_settings["obsfile"]
model_settings = config["model_options"]

In [49]:
model, obs = get_model_obs(model_file, obs_file, ex_settings, model_settings, model_cfg['parameters'] )

/Users/jmissik/Desktop/repos/fetch3_nhl/fetch3/optimize/fetch_wrapper.py:185: FutureWarning:

Indexing a timezone-aware DatetimeIndex with a timezone-naive datetime is deprecated and will raise KeyError in a future version. Use a timezone-aware object instead.



In [50]:
model

array([-3.16732861e+01, -1.11402823e+01, -1.65370529e+00,  2.83875317e+00,
        4.96619622e+00,  5.97337746e+00,  6.44978215e+00,  6.67467919e+00,
        6.78039506e+00,  6.82963518e+00,  6.85211466e+00,  7.25332698e+01,
        1.16806396e+02,  2.80219088e+02,  4.57819475e+02,  6.38198931e+02,
        7.47421751e+02,  8.56236645e+02,  9.32348795e+02,  9.19845929e+02,
        1.01481100e+03,  1.17441722e+03,  1.32823081e+03,  1.38808455e+03,
        1.47470473e+03,  1.49555332e+03,  1.53761509e+03,  1.60037063e+03,
        1.64813826e+03,  1.68615782e+03,  1.72665296e+03,  1.77022444e+03,
        1.78304253e+03,  1.77475780e+03,  1.74410513e+03,  1.71548079e+03,
        1.54049545e+03,  1.27630309e+03,  9.08173267e+02,  4.94926745e+02,
        4.21884172e+02,  2.06231875e+02,  1.01949411e+02,  5.20620665e+01,
        2.83197185e+01,  1.70448357e+01,  1.16954848e+01,  9.15824722e+00,
        7.95465508e+00,  7.38334008e+00,  7.11173998e+00,  6.98220258e+00,
        6.92000086e+00,  

In [51]:
obs

Timestamp
2011-07-06 00:30:00-05:00     20.785242
2011-07-06 01:00:00-05:00     16.077257
2011-07-06 01:30:00-05:00      9.957492
2011-07-06 02:00:00-05:00      7.806856
2011-07-06 02:30:00-05:00      8.656880
                                ...    
2011-07-07 22:00:00-05:00    105.101555
2011-07-07 22:30:00-05:00     82.760854
2011-07-07 23:00:00-05:00     62.477579
2011-07-07 23:30:00-05:00     59.119767
2011-07-08 00:00:00-05:00     48.814445
Name: USA_UMB_CON_Aru_Js_28, Length: 96, dtype: float64

In [52]:
fig = go.Figure()
# Create and style traces
fig.add_trace(go.Scatter(y=model))
fig.add_trace(go.Scatter(y=obs))
fig.show()

In [53]:
scheduler.get_best_parameters()

({'sat_xylem': 0.5454288274049759,
  'scale_nhl': 0.7065906047821044,
  'Root_depth': 3.2,
  'Soil_depth': 5,
  'sand_d': 5.0,
  'clay_d': 4.2,
  'cte_clay': 3,
  'H_init_soilbottom': -6.09,
  'H_init_soilmid': -0.402,
  'H_init_canopytop': -23.3,
  'alpha_1': 0.8,
  'theta_S1': 0.55,
  'theta_R1': 0.068,
  'n_1': 1.5,
  'm_1': 0.33333333333333337,
  'Ksat_1': 1.94e-07,
  'alpha_2': 14.5,
  'theta_S2': 0.47,
  'theta_R2': 0.045,
  'n_2': 2.4,
  'm_2': 0.5833333333333333,
  'Ksat_2': 3.45e-05,
  'theta_1_clay': 0.08,
  'theta_2_clay': 0.12,
  'theta_1_sand': 0.05,
  'theta_2_sand': 0.09,
  'Kr': 7.2e-10,
  'qz': 9,
  'Ksax': 1e-05,
  'Aind_r': 1,
  'kmax': 1e-05,
  'ap': 2e-06,
  'bp': -1500000.0,
  'Phi_0': 574000000.0,
  'p': 20,
  'taper_top': 1.0,
  'sapwood_depth': 2.494584059,
  'dbh': 9.9,
  'stand_density_sp': 161.8037135,
  'Hspec': 17.48,
  'LAI': 0.898266707,
  'mean_crown_area_sp': 34.16,
  'sum_LAI_plot': 3.45,
  'Cd': 0.1,
  'alpha_ml': 0.1,
  'Cf': 0.85,
  'x': 1,
  'Vcma